# read WiGle dataset 

In [1]:
import pandas as pd
from os import listdir, chdir, path

In [2]:
chdir('/Users/nmohan/Documents/Git Code/Anveshak/Datasets')

In [3]:
listdir(".")

['cell_towers.csv',
 'combined_dataset_wigle.csv',
 'map.html',
 'map.png',
 'milan_basestations.csv',
 'MilanBaseStation_Grid',
 'MilanBaseStation_Grid.csv',
 'milano-grid.geojson',
 'opencellid_cell_towers.csv',
 'sms-call-internet-mi-2013-12-01.txt',
 'wigle_combined_dataset.csv',
 'wigledataset_Grid.csv']

In [23]:
wifi_ap = pd.read_csv('combined_dataset_wigle.csv')

print(wifi_ap)

     comment qos         transid    city                       ssid  \
0        NaN   5  20160212-00000     NaN                 Welcome NI   
1        NaN   0  20100426-00000  Milano                    default   
2        NaN   0  20051006-00000  Milano                   FastKris   
3        NaN   0  20090227-00000     NaN                 CasaMilano   
4        NaN   3  20130102-00000  Milano                  belkin54g   
5        NaN   0  20170310-00000     NaN                  WiPG-1000   
6        NaN   0  20170125-00000  Milano           WiPG-MIL-DemoLab   
7        NaN   0  20170222-00000  Milano   IELINK_06:84:22:00:46:47   
8        NaN   0  20140917-00000  Milano                   mnet_001   
9        NaN   0  20080906-00000     NaN            NETWORK_CALDERA   
10       NaN   2  20150425-00000     NaN                CAPADEBOMBA   
11       NaN   0  20120116-00000   Monza           SpeedTouch602271   
12       NaN   2  20150410-00000  Milano                 giovanni57   
13    

## list all headers in the dataset

In [24]:
print list(wifi_ap)

['comment', 'qos', 'transid', 'city', 'ssid', 'encryption', 'wep', 'bcninterval', 'dhcp', 'type', 'channel', 'trilong', 'paynet', 'userfound', 'housenumber', 'lasttime', 'firsttime', 'name', 'lastupdt', 'country', 'region', 'netid', 'freenet', 'trilat', 'road']


## Filter dataset for location coordinates

In [25]:
wifi_ap_locations = wifi_ap[['ssid','trilat','trilong']]

wifi_ap_locations.head()

ssid       trilat     trilong
0  Welcome NI  45.40885925  9.14899635
1     default  45.48382187  9.21443939
2    FastKris  45.48870087  9.21076393
3  CasaMilano  45.42891312  9.10291195
4   belkin54g  45.47829819  9.14686108

In [33]:
wifi_ap_locations1 = wifi_ap_locations[wifi_ap_locations.isnull().any(axis=1)]

print wifi_ap_locations1

     ssid       trilat     trilong
46    NaN  45.48195267  9.21704006
50    NaN  45.51730728  9.11580181
79    NaN  45.45975876  9.10551453
277   NaN  45.45891953  9.10587883
284   NaN   45.5120163  9.21131516
305   NaN  45.46778107  9.22380352
313   NaN  45.48151398  9.19275188
360   NaN  45.45255661  9.16522121
471   NaN  45.48667908  9.20436192
537   NaN  45.46035004  9.10582161
540   NaN  45.45977402  9.10555077
594   NaN  45.46035385  9.10620308
595   NaN  45.46054077  9.10601234
596   NaN   45.4603157  9.10578823
609   NaN  45.46030045  9.10611916
610   NaN  45.46021271  9.10571575
611   NaN    45.460289   9.1062336
658   NaN  45.47642136  9.22893715
667   NaN  45.49761963  9.10735416
1562  NaN   45.4834671  9.16037083
1828  NaN  45.43346786  9.23956299
2355  NaN  45.46544266   9.2084589
2455  NaN  45.45133972  9.20234871
2495  NaN  45.49202728  9.21846771
2530  NaN  45.46569824  9.19015121
2533  NaN  45.46127701  9.16928959
2535  NaN  45.43008804   9.1730175
2542  NaN  45.491870

In [26]:
wifi_ap_locations = wifi_ap_locations.dropna(subset=['trilat'])
wifi_ap_locations = wifi_ap_locations.dropna(subset=['trilong'])

# plot gps coordinates to a map

In [27]:
import folium
from folium import plugins
map_osm = folium.Map(width=1100,height=1000,location=[45.4674, 9.1887], zoom_start=12)
#map_osm.add_child(folium.LatLngPopup())

In [19]:
map_osm

## mark latitude and longitude locations to map

In [28]:
import ast
import math

latitude = wifi_ap_locations.trilat.tolist()
longitude = wifi_ap_locations.trilong.tolist()

# remove all stupid text
latitude = list(filter(lambda x: x!= 'trilat', latitude))
longitude = list(filter(lambda x: x!= 'trilong', longitude))

In [29]:
coordinates = map(lambda x,y:[float(x),float(y)],latitude,longitude)

print coordinates[1][0]
print coordinates[1][1]

45.48382187
9.21443939


In [30]:
map_osm = folium.Map(location=[coordinates[1][0], coordinates[1][1]], zoom_start=11)
#map_osm = folium.Map(zoom_start=11)

map_osm

In [31]:
for i in range(0, len(coordinates)):
    folium.RegularPolygonMarker([coordinates[i][0], coordinates[i][1]], radius=5).add_to(map_osm)
    
map_osm

In [32]:
map_osm.add_child(plugins.HeatMap(coordinates, radius=15))

In [ ]:
folium.TileLayer('stamenwatercolor').add_to(map_osm)
map_osm

In [20]:
folium.TileLayer('openstreetmap').add_to(map_osm)
map_osm

In [21]:
map_osm.save("map.html")

In [ ]:
#System.setProperty("webdriver.chrome.driver", "/Users/nmohan/chromedriver");

## How to convert saved Map HTML to PNG for export

### Take a screenshot

1. First open the HTML code with sublime and add "zoomControl: false" in map declaration 
2. open in browser and screenshot

In [22]:
import os
import time
from selenium import webdriver

delay=5
fn='map.html' #'wifiAP.html'
tmpurl='file://{path}/{mapfile}'.format(path=os.getcwd(),mapfile=fn)
map_osm.save(fn)

browser = webdriver.Chrome("/Users/nmohan/chromedriver")
browser.get(tmpurl)
#Give the map tiles some time to load
time.sleep(delay)
browser.save_screenshot('map.png')
browser.quit()

# Read OpenCellID dataset and map

In [33]:
base_stations = pd.read_csv('opencellid_cell_towers.csv')

In [34]:
print list(base_stations)

['radio', 'mcc', 'net', 'area', 'cell', 'unit', 'lon', 'lat', 'range', 'samples', 'changeable', 'created', 'updated', 'averageSignal']


## Filter all base stations that lie in Milan area 

### Bounding box -> LAT: 45.3588 - 45.567795 ; LONG: 9.011491 - 9.309677

In [35]:
milan_basestations = base_stations[(base_stations.lat >= 45.358801) & (base_stations.lat <= 45.567795) & (base_stations.lon >= 9.011491) & (base_stations.lon <= 9.309677)]

## Remove all base stations except those which are LTE and do not have the same cell

In [36]:
milan_basestations = milan_basestations[(milan_basestations.radio == 'LTE') & (milan_basestations.range >= 1200)]

milan_basestations = milan_basestations.drop_duplicates(['cell'])

### Save the filtered dataset to CSV

In [37]:
milan_basestations.to_csv('milan_basestations.csv')

## Get the coordinates

In [38]:
BS_latitude = milan_basestations.lat.tolist()
BS_longitude = milan_basestations.lon.tolist()

In [39]:
BS_coordinates = map(lambda x,y:[float(x),float(y)],BS_latitude,BS_longitude)

## Map the coordinates on the map

In [40]:
map_bs = folium.Map(width=1100,height=1000,location=[45.4674, 9.1887], zoom_start=12)

In [41]:
map_bs

In [42]:
map_bs.add_child(plugins.HeatMap(BS_coordinates, radius=15))

In [225]:
map_bs.save("BaseStations.html")